In [3]:
# Transformers installation
! pip install transformers datasets
# To install from source instead of the last release, comment the command above and uncomment the following one.
# ! pip install git+https://github.com/huggingface/transformers.git

  Using cached scikit-learn-1.0.1.tar.gz (6.6 MB)
  Installing build dependencies ... - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / - \ | / error
  ERROR: Command errored out with exit status 1:
   command: /Users/lucas-andreithil/mambaforge/bin/python3.9 /private/var/folders/z7/8t7cnys53zng5b98fknc2qb00000gn/T/pip-standalone-pip-01b25oyn/__env_pip__.zip/pip install --ignore-installed --no-user --prefix /private/var/folders/z7/8t7cnys53zng5b98fknc2qb00000gn/T/pip-build-env-__7wq0uv/overlay --no-warn-script-location --no-binary :none: --only-binary :none: -i https://pypi.org/simple -- setuptools wheel 'Cython>=0.28.5' 'oldest-supported-numpy; python_version!='"'"'3.7'"'"' or platform_machine=='"'"'aarch64'"'"'

In [1]:
import pandas as pd
import datasets
from datasets import Dataset

In [15]:
import pandas as pd
file = pd.read_csv("train_df10000.csv")
file.head()

print(len(file)/3)

LABEL_LIST = ["O", "B-LAW", "I-LAW", "B-CARDINAL", "I-CARDINAL", "B-DATE", "I-DATE", "B-GPE", "I-GPE", "B-ORG", "I-ORG", "B-WORK_OF_ART", "I-WORK_OF_ART", "B-PERSON", "I-PERSON", "B-NORP", "I-NORP", "B-LOC", "I-LOC"]
LABEL_INT = [i for i in range(len(LABEL_LIST))]
print(len(LABEL_LIST))
print(LABEL_INT)

5920396.666666667
19
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18]


In [52]:
clean_data = []
clean_labels = []
# Loop over and create DatasetDict with Datasets inside

for line in file['Entities'][:5920396]:

    line = line.split(" ")
    if line[0] == "":
        line[0] = " "

    label = ""
    if(line[2] != ''):
        line[1] = line[1] + "-" + line[2]

    clean_data.append(line[0])
    clean_labels.append(line[1])

print(clean_data[:20])
print(clean_labels[:20])

# Replace labels with ints
for i in range(len(clean_labels)):
    label = clean_labels[i]
    flag = True
    for j in range(len(LABEL_LIST)):
        if label == LABEL_LIST[j]:
            clean_labels[i] = LABEL_INT[j]
            flag = False
    if flag:
        clean_labels[i] = 0

print(clean_labels[:20])


clean_data = pd.DataFrame(clean_data)
clean_labels = pd.DataFrame(clean_labels)

shuffle_df = clean_data.sample(frac=1)
train_size = int(0.7 * len(clean_data))
# Split your dataset
X_train = shuffle_df[:train_size]
X_test = shuffle_df[train_size:]

shuffle_df = clean_labels.sample(frac=1)
y_train = shuffle_df[:train_size]
y_test = shuffle_df[train_size:]

print(X_train.values.tolist()[:10])
X_train = X_train.values.tolist()
print("X_train")
x2 = []
for value in X_train:
    x2.append(str(value[0]))
X_train = x2
x2 = []
for value in y_train.values.tolist():
    x2.append(value[0])
y_train = x2
x2 = []
for value in X_test.values.tolist():
    x2.append(str(value[0]))
X_test = x2
x2 = []
for value in y_test.values.tolist():
    x2.append(value[0])
y_test = x2
x2 = []
for value in clean_data.values.tolist():
    x2.append(value[0])
clean_data = x2
x2 =[]
for value in clean_labels.values.tolist():
    x2.append(value[0])
clean_labels = x2


dataset_df_train = pd.DataFrame({'text':X_train, 'label':y_train})
clean_data_df_train = Dataset.from_pandas(dataset_df_train)

dataset_df_test = pd.DataFrame({'text':X_test, 'label':y_test})
clean_data_df_test = Dataset.from_pandas(dataset_df_test)

dataset_df_unsupervised = pd.DataFrame({'text':X_test, 'label':y_test})
dataset_df_unsupervised = Dataset.from_pandas(dataset_df_unsupervised)

[' ', 'FOURTH', 'SECTION', ' ', 'CASE', 'OF', 'POHOSKA', 'v.', ' ', '(', 'Application', 'no', '.', '33530/06', ')', ' ', 'JUDGMENT', ' ', '10', 'January']
['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-CARDINAL', 'O', 'O', 'O', 'O', 'B-DATE', 'I-DATE']
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 0, 0, 0, 0, 5, 6]
[['him'], ['been'], ['by'], ['in'], ['fill'], ['3'], ['the'], ['the'], ['.'], ['community']]
X_train


In [53]:
print(dataset_df_train.head(20))
print(clean_data_df_train.column_names)

#clean_data_df_train = Dataset({dataset_df_train})
#clean_data_df_test = Dataset.from_pandas(clean_data_df_test)

           text  label
0           him      0
1          been      0
2            by      0
3            in      0
4          fill      0
5             3      0
6           the      0
7           the      0
8             .      0
9     community      3
10           22      0
11  authorities      0
12            8      0
13            )      0
14     pressure      0
15            .      0
16     interest      4
17        after      0
18        Party      9
19         this      0
['text', 'label']


In [54]:
from transformers import AutoTokenizer

#tokenizer = AutoTokenizer.from_pretrained("bert-base-cased")
tokenizer = AutoTokenizer.from_pretrained("nlpaueb/legal-bert-base-uncased")



loading configuration file https://huggingface.co/nlpaueb/legal-bert-base-uncased/resolve/main/config.json from cache at /Users/lucas-andreithil/.cache/huggingface/transformers/8fb343045f345372593fb03cc8edd339757b9b5fa164bfd4a071c33d81906423.81e683d6e4f3240a109c9cfd0742b01d443acc6fc2b120b20796fb85ddf0f393
Model config BertConfig {
  "architectures": [
    "BertForPreTraining"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "classifier_dropout": null,
  "eos_token_ids": 0,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "output_past": true,
  "pad_token_id": 0,
  "position_embedding_type": "absolute",
  "transformers_version": "4.12.3",
  "type_vocab_size": 2,
  "use_cache": true,
  "vocab_size": 30522
}

loading file https://huggingface.co/nl

In [55]:
# Process our own dataset:
dataset = datasets.DatasetDict({'train': clean_data_df_train, 'test': clean_data_df_test, 'unsupervised': dataset_df_unsupervised})

print(dataset.column_names)

{'train': ['text', 'label'], 'test': ['text', 'label'], 'unsupervised': ['text', 'label']}


In [90]:
# padding="max_length",
def tokenize_function(examples):
    return tokenizer(examples["text"],  truncation=True)

tokenized_datasets = dataset.map(tokenize_function, batched=True)

  0%|          | 0/4145 [00:00<?, ?ba/s]

  0%|          | 0/1777 [00:00<?, ?ba/s]

  0%|          | 0/1777 [00:00<?, ?ba/s]

In [91]:
small_train_dataset = tokenized_datasets["train"].shuffle(seed=42).select(range(1000))
small_eval_dataset = tokenized_datasets["test"].shuffle(seed=42).select(range(1000))
full_train_dataset = tokenized_datasets["train"]
full_eval_dataset = tokenized_datasets["test"]

In [92]:
from transformers import AutoModelForSequenceClassification

model = AutoModelForSequenceClassification.from_pretrained("nlpaueb/legal-bert-base-uncased", num_labels=19)

loading configuration file https://huggingface.co/nlpaueb/legal-bert-base-uncased/resolve/main/config.json from cache at /Users/lucas-andreithil/.cache/huggingface/transformers/8fb343045f345372593fb03cc8edd339757b9b5fa164bfd4a071c33d81906423.81e683d6e4f3240a109c9cfd0742b01d443acc6fc2b120b20796fb85ddf0f393
Model config BertConfig {
  "architectures": [
    "BertForPreTraining"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "classifier_dropout": null,
  "eos_token_ids": 0,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "id2label": {
    "0": "LABEL_0",
    "1": "LABEL_1",
    "2": "LABEL_2",
    "3": "LABEL_3",
    "4": "LABEL_4",
    "5": "LABEL_5",
    "6": "LABEL_6",
    "7": "LABEL_7",
    "8": "LABEL_8",
    "9": "LABEL_9",
    "10": "LABEL_10",
    "11": "LABEL_11",
    "12": "LABEL_12",
    "13": "LABEL_13",
    "14": "LABEL_14",
    "15": "LABEL_15",
    "16": "LABEL_16",
    "17": "LABEL_17",
    "18": "LABEL_18"
  },
  "initial

In [93]:
from transformers import TrainingArguments

training_args = TrainingArguments("test_trainer")


PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).


In [102]:
from transformers import Trainer

trainer = Trainer(
    model=model, args=training_args, train_dataset=small_train_dataset, eval_dataset=small_eval_dataset
)

In [103]:
trainer.train()


The following columns in the training set  don't have a corresponding argument in `BertForSequenceClassification.forward` and have been ignored: text.
***** Running training *****
  Num examples = 1000
  Num Epochs = 3
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 8
  Gradient Accumulation steps = 1
  Total optimization steps = 375


ValueError: expected sequence of length 4 at dim 1 (got 3)